In [1]:
from pypdf import PdfReader
import re
import string
import os
from termcolor import colored

In [8]:
def is_newspaper_name(line):
    words = line.split()
    if len(words) > 0:
        return len(words) < 5 and line[-1] not in string.punctuation
    else:
        return False

In [3]:
def replace_space_punct(chaine):
    # Créer un motif pour les espaces et les ponctuations
    motif = f"[{re.escape(string.punctuation)} ]+"
    # Remplacer les espaces et les ponctuations par un seul tiret
    resultat = re.sub(motif, "-", chaine)
    resultat = re.sub('’', "-", resultat)
    # Supprimer le tiret à la fin de la chaîne si présent
    return resultat.rstrip("-")

In [16]:
def article2txt(pdf_path, month:str, year:str) :
    reader = PdfReader(pdf_path)
    new_page = True
    folder = 'Sources/Europresse/txt/'+month+'_'+year
    os.makedirs(folder, exist_ok = True)
    for page in reader.pages:
        current_text = page.extract_text()
        if "Ce document référence un lien URL de site non hébergé par Cision." in current_text:
            print("Ce document référence un lien URL de site non hébergé par Cision.")
            continue
    
        text_lines = current_text.split("\n")
    
        if new_page and len(text_lines) > 3:
            content = ''
            newspaper = replace_space_punct(text_lines[0]) #on considère que le nom du journal est en première ligne et le titre de l'article en 4e ligne
            title = replace_space_punct(text_lines[3])
            first_line_num = 3
        else:
            first_line_num = 0
    
        while "-Aussi paru dans" in text_lines[-1] or is_newspaper_name(text_lines[-1]): #supprime les mentions de parution dans d'autres journaux
            text_lines.pop()
            try:
                text_lines[-1]
            except IndexError :
                print(colored("Erreur avec la lecture d'une ligne", 'red'))
                break
    
        for line_num in range(first_line_num, len(text_lines)):
            has_copyright = ('© ' in text_lines[line_num] and year in text_lines[line_num]) or ("Le présent document est protégé par les lois et conventions internationales sur le droit d'auteur et son utilisation est régie par ces lois et conventions" in text_lines[line_num])
            if not has_copyright and len(text_lines) > 3:
                content = content + ' ' + text_lines[line_num]
                if line_num == len(text_lines) - 1:
                    new_page = False
            else:
                #filename = PREF_POL_AUTEUR_ANNEE_MOIS_TITRE.[pdf/txt]
                pref = 'NEW_UNK_' + newspaper + '_' + year + '_' + month + '_'
                filename = folder + '/' + pref + title + '.txt'

                
                while True:
                    try:
                        i = 2
                        while(os.path.isfile(filename)):
                            filename = folder + '/' + pref + title + str(i) + '.txt'
                            i = i + 1
                        with open(filename, 'w+', encoding='utf-8') as f:
                            f.write(content)
                            print(f"Fichier {filename} enregistré")
                            break
                    except OSError as exc:
                        if exc.errno == 36 and len(title) !=0:
                            title = title[0:int(len(title)/2)]
                            filename_tmp = 'NEW_UNK_' + newspaper + '_' + year + '_' + month + '_' + title + '.txt'
                            filename = folder + '/' + filename_tmp
                        else:
                            print("Erreur avec l'enregistrement du fichier")
                            break
                new_page = True
                break
            
            
        

In [10]:
for year in range(2019, 2025) :
    path = 'Sources/Europresse/pdf_print/' + str(year) + '/'
    for month in range(1, 13):
        month = str(month) if month > 9 else '0' + str(month)
        file = path + month + '_' + str(year) + '.pdf'
        if os.path.isfile(file):
            print(f"Ouverture fichier {file}")
            article2txt(file, month, str(year))
        i = 2
        while os.path.isfile(path + month + '_' + str(year) + '_' + str(i) + '.pdf'):
            print(f"Ouverture fichier {file}")
            article2txt(file, month, str(year))
            i = i + 1

Ouverture fichier Sources/Europresse/pdf_print/2022/01_2022.pdf
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Le-Monde_2022_01_La-prostitution-en-débat-au-procès-du-meurtre-de-Vanesa-Campos.txt enregistré
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Le-Monde-site-web_2022_01_Fatoumata-Sillah.txt enregistré
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Le-Télégramme-Bretagne_2022_01_Pour-Nikita-«-la-prostitution-peut-être-choisie-».txt enregistré
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Libération_2022_01_Vanesa-Campos-la-survie-ou-la-mort.txt enregistré
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Le-Journal-de-Montréal_2022_01_DOMINIQUE-SCALI.txt enregistré
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Courrier-picard_2022_01_Aujourd-hui.txt enregistré
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Libération-site-web_2022_01_prostitution.txt enregistré
Fichier Sources/Europresse/txt/01_2022/NEW_UNK_Courrier-picard_2022_01_Aujourd-hui2.txt enregistré
Fichier Sources/Europ

In [23]:
article2txt('Sources/Europresse/pdf_print/2021/12_2021.pdf', '12', '2021')

Fichier Sources/Europresse/txt/12_2021/NEW_UNK_Presse-Océan_2021_12_«-Le-travail-du-sexe-s-est-réorganisé-».txt enregistré
Fichier Sources/Europresse/txt/12_2021/NEW_UNK_Presse-Océan-site-web_2021_12_A-H-D.txt enregistré
Fichier Sources/Europresse/txt/12_2021/NEW_UNK_Le-Monde_2021_12_Hakima-Himmich-et-Camille-Spire-Comment-comprendre-que-plus-de-680-000-personnes-sont.txt enregistré
Fichier Sources/Europresse/txt/12_2021/NEW_UNK_La-Provence_2021_12_-Face-à-la-mort-on-a-dû-prendre-notre-destin-en-main.txt enregistré
Fichier Sources/Europresse/txt/12_2021/NEW_UNK_La-Presse_2021_12_Rose-Aimée-Automne-T-Morin.txt enregistré
Fichier Sources/Europresse/txt/12_2021/NEW_UNK_Métro-Vaudreuil-Soulanges-QC-site-web-Métro-Montréal_2021_12_Ce-vendredi-17-décembre-a-lieu-la-Journée-internationale-pour-l-élimination-des-violences-faites-aux-travailleuses-et.txt enregistré
Fichier Sources/Europresse/txt/12_2021/NEW_UNK_Métro-Le-Plateau-QC-site-web_2021_12_Quentin-Dufranne.txt enregistré
Fichier Sources